In [1]:
print("Hello world")

Hello world


# Smart search model 1

In [2]:
import pandas as pd

df = pd.read_csv("freelancers_dataset_specialized_new.csv")

df.shape

(10000, 9)

In [5]:
print(df.isnull().sum())

Freelancer_ID          0
Skills                 0
Experience_Level       0
Years_of_Experience    0
Description            0
Projects               0
Budget_Hourly          0
Budget_Project         0
Location               0
dtype: int64


In [9]:
df.fillna("",inplace=True) # for replaciong missing but there is no null values its just for precaution

df.drop_duplicates(inplace=True)

df["Skills"] = df["Skills"].str.lower().str.strip()
df["Description"] = df["Description"].str.lower().str.strip()

df["text"] = df["Skills"] + " " + df["Description"]


In [10]:
df.to_csv("Smart_search_cleaned_dataset.csv", index=False)

In [19]:
import pandas as pd

df = pd.read_csv("Smart_search_cleaned_dataset.csv")

df.head(5)



Freelancer_ID                                             Skills  \
0         F0001  mobile development: hybrid app development, an...   
1         F0002  education & training: training online lms, lea...   
2         F0003  cybersecurity: information security consultati...   
3         F0004  education & training: training, teaching; gene...   
4         F0005  devops: azure blockchain service, azure app se...   

  Experience_Level  Years_of_Experience  \
0      Entry Level                    4   
1     Intermediate                    3   
2     Intermediate                    6   
3           Expert                   12   
4     Intermediate                    5   

                                         Description  \
0  entry level mobile development professional wi...   
1  intermediate education & training professional...   
2  intermediate cybersecurity professional with e...   
3  expert education & training professional with ...   
4  intermediate devops professional with experien...   

                                            Projects  Budget_Hourly  \
0      There go any water only event. for George Ltd              6   
1  For too information. for Smith LLC; Reduce sou...             18   
2  Include quality stay. for Hill and Sons; Watch...             15   
3  Yet response family green these. for Brown-Mor...             39   
4  Defense myself foot both since. for Stone-Gain...             15   

  Budget_Project   Location                                               text  
0      $236-$859    Kolkata  mobile development: hybrid app development, an...  
1     $514-$2068       Pune  education & training: training online lms, lea...  
2    $1336-$2228       Pune  cybersecurity: information security consultati...  
3    $4680-$7568  Bangalore  education & training: training, teaching; gene...  
4    $1410-$2586    Kolkata  devops: azure blockchain service, azure app se...

In [20]:
import pandas as pd

df = pd.read_csv("Smart_search_cleaned_dataset.csv")

df.shape

(10000, 10)

In [2]:
from langchain.docstore.document import Document
import pandas as pd

df = pd.read_csv("Smart_search_cleaned_dataset.csv")
# Convert CSV rows into LangChain documents
docs = [Document(page_content=row["text"]) for _, row in df.iterrows()]

print(f"Loaded {len(docs)} documents for FAISS indexing.")

Loaded 10000 documents for FAISS indexing.


In [2]:
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.vectorstores import FAISS
from langchain_huggingface import HuggingFaceEmbeddings
from langchain.schema import Document
import pandas as pd
import os

os.environ["HF_HUB_DISABLE_SYMLINKS_WARNING"] = "1"

df = pd.read_csv("Smart_search_cleaned_dataset.csv")

docs = [Document(page_content=row["text"]) for _, row in df.iterrows()]

# Use Hugging Face's free embedding model
embedding_model = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")

# Store in FAISS index
faiss_index = FAISS.from_documents(docs, embedding_model)

# Save FAISS index locally
faiss_index.save_local("faiss_index")

print("FAISS index created using Hugging Face embeddings.")

FAISS index created using Hugging Face embeddings.


In [ ]:
#Just a trial part to check if the faiss is loaded or not

import os
from langchain_huggingface import HuggingFaceEmbeddings
from langchain.vectorstores import FAISS

# Fix Hugging Face symlink warning
os.environ["HF_HUB_DISABLE_SYMLINKS_WARNING"] = "1"

# Load embedding model
embedding_model = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")

# ✅ Load FAISS index safely
new_faiss_index = FAISS.load_local("faiss_index", embedding_model, allow_dangerous_deserialization=True)

# ✅ Test similarity search
query = "AI freelancer search"
results = new_faiss_index.similarity_search(query, k=5)

for r in results:
    print(r.page_content)

writing & content creation: content seo, research papers; general: api expert writing & content creation professional with experience in content seo, research papers.
web development: web crawling, php; general: expert web development professional with experience in web crawling, php.
web development: interactive design, web crawling, database, wordpress plugin; general: api expert web development professional with experience in interactive design, web crawling, database, wordpress plugin.
web development: web crawling, laravel, software architecture & design, react; general: api, git expert web development professional with experience in web crawling, laravel, software architecture & design, react.
web development: web crawling, laravel, web scraping framework; general: expert web development professional with experience in web crawling, laravel, web scraping framework.


In [15]:
from langchain_elasticsearch import ElasticsearchStore
from langchain_huggingface import HuggingFaceEmbeddings
from elasticsearch import Elasticsearch

# Connect to Elasticsearch (with SSL verification disabled)
es_url = "https://localhost:9200"  
es = Elasticsearch(
    es_url,
    basic_auth=("elastic", "fT3WSy=x=G-5dpSkBEB_"),
    verify_certs=False,
    ssl_show_warn=False
)

# Define the index name
es_index_name = "freelancers"

# Define the embedding model
embedding_model = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")


es_store = ElasticsearchStore(
    index_name=es_index_name,
    es_url=es_url,  # Pass the Elasticsearch client
    embedding=embedding_model
)


TlsError: TLS error caused by: TlsError(TLS error caused by: SSLError([SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed: self-signed certificate in certificate chain (_ssl.c:1000)))

# Smart search model 2


In [3]:
from llama_index.core import SimpleDirectoryReader, Document
import pandas as pd

# Load dataset
df = pd.read_csv("Smart_search_cleaned_dataset.csv")

# Convert CSV rows into LlamaIndex Documents
docs = [Document(text=row["text"]) for _, row in df.iterrows()]

print(f"Loaded {len(docs)} documents for FAISS indexing.")


Loaded 10000 documents for FAISS indexing.


In [21]:
from llama_index.core import VectorStoreIndex, Settings
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.core.schema import TextNode  # <-- Use TextNode directly
import pandas as pd

# Load the dataset
df = pd.read_csv("Smart_search_cleaned_dataset.csv")

# Initialize Hugging Face embedding model
embedding_model = HuggingFaceEmbedding(model_name="sentence-transformers/all-MiniLM-L6-v2")
Settings.embed_model = embedding_model

# Convert CSV rows into TextNode objects with explicit IDs
nodes = []
for _, row in df.iterrows():
    doc_id = row["Freelancer_ID"]
    node = TextNode(
        text=row["text"], 
        id_=doc_id  # <-- Explicitly set the node ID
    )
    nodes.append(node)
    print(f"Creating FAISS Node with ID: {doc_id}")

# Create the FAISS index directly from nodes (NOT from_documents)
index = VectorStoreIndex(nodes)  # <-- Pass nodes directly

# Save the FAISS index
index.storage_context.persist(persist_dir="faiss_index_llama")

print("FAISS index created with custom IDs.")

Creating FAISS Node with ID: F0001
Creating FAISS Node with ID: F0002
Creating FAISS Node with ID: F0003
Creating FAISS Node with ID: F0004
Creating FAISS Node with ID: F0005
Creating FAISS Node with ID: F0006
Creating FAISS Node with ID: F0007
Creating FAISS Node with ID: F0008
Creating FAISS Node with ID: F0009
Creating FAISS Node with ID: F0010
Creating FAISS Node with ID: F0011
Creating FAISS Node with ID: F0012
Creating FAISS Node with ID: F0013
Creating FAISS Node with ID: F0014
Creating FAISS Node with ID: F0015
Creating FAISS Node with ID: F0016
Creating FAISS Node with ID: F0017
Creating FAISS Node with ID: F0018
Creating FAISS Node with ID: F0019
Creating FAISS Node with ID: F0020
Creating FAISS Node with ID: F0021
Creating FAISS Node with ID: F0022
Creating FAISS Node with ID: F0023
Creating FAISS Node with ID: F0024
Creating FAISS Node with ID: F0025
Creating FAISS Node with ID: F0026
Creating FAISS Node with ID: F0027
Creating FAISS Node with ID: F0028
Creating FAISS Node 

In [14]:
from llama_index.embeddings.huggingface import HuggingFaceEmbedding

embedding_model = HuggingFaceEmbedding(model_name="sentence-transformers/all-MiniLM-L6-v2")
vector = embedding_model.get_text_embedding("Test sentence")
print("Embedding generated successfully:", vector[:5])  # Print first 5 values


Embedding generated successfully: [0.0429728627204895, 0.09663482010364532, -0.002129176165908575, 0.07826834917068481, -0.006417416967451572]


In [10]:
from elasticsearch import Elasticsearch
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
import pandas as pd
import torch

# Elasticsearch Connection
es_client = Elasticsearch(
    "https://localhost:9200",
    basic_auth=("elastic", "fT3WSy=x=G-5dpSkBEB_"),
    verify_certs=False
)

es_index_name = "freelancers"

# Embedding Model
device = "cuda" if torch.cuda.is_available() else "cpu"
embedding_model = HuggingFaceEmbedding(
    model_name="sentence-transformers/all-MiniLM-L6-v2",
    device=device
)

# Load Data
df = pd.read_csv("Smart_search_cleaned_dataset.csv")

# Index Data
for _, row in df.iterrows():
    doc_id = row["Freelancer_ID"]
    text = row["text"]
    embedding = embedding_model.get_text_embedding(text)

    document = {
        "text": text,
        "text_embedding": embedding,
    }

    es_client.index(index=es_index_name, id=doc_id, document=document)

print("✅ Elasticsearch index created successfully!")

C:\Users\Varun\AppData\Roaming\Python\Python312\site-packages\elasticsearch\_sync\client\__init__.py:403: SecurityWarning: Connecting to 'https://localhost:9200' using TLS with verify_certs=False is insecure
  _transport = transport_class(
C:\Users\Varun\AppData\Roaming\Python\Python312\site-packages\urllib3\connectionpool.py:1099: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
C:\Users\Varun\AppData\Roaming\Python\Python312\site-packages\urllib3\connectionpool.py:1099: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
C:\Users\Varun\AppData\Roaming\Python\Python312\site-packages\urllib3\connectionpool.py:1099: InsecureRequ

✅ Elasticsearch index created successfully!


C:\Users\Varun\AppData\Roaming\Python\Python312\site-packages\urllib3\connectionpool.py:1099: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
C:\Users\Varun\AppData\Roaming\Python\Python312\site-packages\urllib3\connectionpool.py:1099: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


In [2]:
from elasticsearch import Elasticsearch
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.core import StorageContext, load_index_from_storage
from llama_index.core import Settings

# Disable LLM globally to avoid OpenAI API key requirement
Settings.llm = None

# Initialize Elasticsearch client
es_client = Elasticsearch(
    "https://localhost:9200",
    basic_auth=("elastic", "fT3WSy=x=G-5dpSkBEB_"),
    verify_certs=False  # Security Warning: Avoid in production!
)

# Initialize embedding model (only once)
embedding_model = HuggingFaceEmbedding(model_name="sentence-transformers/all-MiniLM-L6-v2", device="cpu")

# Load FAISS index (LlamaIndex version)
persist_dir = "faiss_index_llama"
storage_context = StorageContext.from_defaults(persist_dir=persist_dir)
faiss_index_llama = load_index_from_storage(storage_context, embed_model=embedding_model, llm=None)

def hybrid_faiss_es_search(query_text, faiss_index_llama, es_client, embedding_model, index_name="freelancers", top_k=10):
    """
    Performs a hybrid search using LlamaIndex FAISS index and Elasticsearch.
    """
    # 1. FAISS Retrieval (using LlamaIndex)
    query_embedding = embedding_model.get_query_embedding(query_text)
    
    # Create query engine with llm=None to disable LLM usage
    query_engine = faiss_index_llama.as_query_engine(
        similarity_top_k=top_k,
        llm=None  # Explicitly disable LLM
    )
    response = query_engine.query(query_text)  # Pass the text, not embedding
    nodes_with_scores = response.source_nodes
    faiss_node_ids = [node.node.id_ for node in nodes_with_scores]  # Use id_ instead of node_id
    print("FAISS node IDs:", faiss_node_ids)

    # 2. Elasticsearch Refinement
    es_query = {
        "query": {
            "bool": {
                "must": [
                    {
                        "ids": {
                            "values": faiss_node_ids  # Use FAISS node IDs
                        }
                    },
                    {
                        "bool": {
                            "should": [
                                {
                                    "match": {
                                        "text": query_text
                                    }
                                },
                                {
                                    "script_score": {
                                        "query": {
                                            "exists": {
                                                "field": "text_embedding"
                                            }
                                        },
                                        "script": {
                                            "source": "cosineSimilarity(params.query_vector, 'text_embedding') + 1.0",
                                            "params": {
                                                "query_vector": query_embedding  # Use the computed query embedding
                                            }
                                        },
                                        "boost": 2.0  # Adjust boost for vector score importance
                                    }
                                }
                            ]
                        }
                    }
                ]
            }
        }
    }

    print("Elasticsearch Query:", es_query)  # Debug print
    es_results = es_client.search(index=index_name, body=es_query)
    predicted_ids = [hit['_id'] for hit in es_results['hits']['hits']]
    print("Predicted Document IDs:", predicted_ids)

    # 3. Result Combination and Re-ranking
    # Use the Elasticsearch score as the final score
    return es_results

# Example usage
search_term = "python developer with skills"
final_results = hybrid_faiss_es_search(search_term, faiss_index_llama, es_client, embedding_model)
print(final_results)

LLM is explicitly disabled. Using MockLLM.


C:\Users\Varun\AppData\Roaming\Python\Python312\site-packages\elasticsearch\_sync\client\__init__.py:403: SecurityWarning: Connecting to 'https://localhost:9200' using TLS with verify_certs=False is insecure
  _transport = transport_class(


FAISS node IDs: ['F7018', 'F8439', 'F8305', 'F5486', 'F0750', 'F5056', 'F1783', 'F0263', 'F3094', 'F3213']
Elasticsearch Query: {'query': {'bool': {'must': [{'ids': {'values': ['F7018', 'F8439', 'F8305', 'F5486', 'F0750', 'F5056', 'F1783', 'F0263', 'F3094', 'F3213']}}, {'bool': {'should': [{'match': {'text': 'python developer with skills'}}, {'script_score': {'query': {'exists': {'field': 'text_embedding'}}, 'script': {'source': "cosineSimilarity(params.query_vector, 'text_embedding') + 1.0", 'params': {'query_vector': [-0.03389541804790497, 0.004716781433671713, -0.03282008692622185, 0.05846158415079117, -0.06667544692754745, -0.11931566894054413, 0.04056127369403839, 0.0393589586019516, -0.10782128572463989, -0.026901347562670708, -0.03365606814622879, 0.004443340469151735, 0.022201664745807648, 0.05251632630825043, 0.031262319535017014, 0.05334049090743065, -0.08885405957698822, 0.03106061927974224, 0.005930518265813589, -0.14014597237110138, -0.04200206324458122, 0.0380057208240032

C:\Users\Varun\AppData\Roaming\Python\Python312\site-packages\urllib3\connectionpool.py:1099: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Predicted Document IDs: ['F0263', 'F7018', 'F8305', 'F8439', 'F1783', 'F5486', 'F0750', 'F5056', 'F3094', 'F3213']
{'took': 554, 'timed_out': False, '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0}, 'hits': {'total': {'value': 10, 'relation': 'eq'}, 'max_score': 12.716075, 'hits': [{'_index': 'freelancers', '_id': 'F0263', '_score': 12.716075, '_source': {'text': 'data science: python, dashboard; general: expert data science professional with experience in python, dashboard.', 'text_embedding': [-0.05550748482346535, -0.025352515280246735, -0.03335467353463173, 0.03034111298620701, -0.023205934092402458, -0.16709811985492706, -0.014108714647591114, 0.07102683186531067, -0.0977114737033844, 0.006761893630027771, -0.0600254125893116, -0.0445309653878212, 0.07279666513204575, 0.0016906082164496183, 0.005556327290832996, 0.037715844810009, -0.05680515617132187, -0.08943638950586319, -0.006240318063646555, -0.107554592192173, -0.03724471107125282, -0.009517660364508629, -

In [25]:
# Example: Query the FAISS index to verify node IDs
query_engine = index.as_query_engine()
response = query_engine.query("python developer with skills")
nodes_with_scores = response.source_nodes
for node in nodes_with_scores:
    print("Node ID:", node.node.id_)

Node ID: F7018
Node ID: F8439


In [12]:
import joblib
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.core import StorageContext, load_index_from_storage, Settings
from elasticsearch import Elasticsearch


Settings.llm = None 

embedding_model = HuggingFaceEmbedding(model_name="sentence-transformers/all-MiniLM-L6-v2")
storage_context = StorageContext.from_defaults(persist_dir="faiss_index_llama")
faiss_index_llama = load_index_from_storage(storage_context, embed_model=embedding_model, llm=None)


def hybrid_faiss_es_search(query_text, faiss_index_llama, es_client, embedding_model, index_name="freelancers", top_k=10):
    """
    Performs a hybrid search using LlamaIndex FAISS index and Elasticsearch.
    """
    # 1. FAISS Retrieval (using LlamaIndex)
    query_embedding = embedding_model.get_query_embedding(query_text)
    
    # Create query engine with llm=None to disable LLM usage
    query_engine = faiss_index_llama.as_query_engine(
        similarity_top_k=top_k,
        llm=None  # Explicitly disable LLM
    )
    response = query_engine.query(query_text)  # Pass the text, not embedding
    nodes_with_scores = response.source_nodes
    faiss_node_ids = [node.node.id_ for node in nodes_with_scores]  # Use id_ instead of node_id
    print("FAISS node IDs:", faiss_node_ids)

    # 2. Elasticsearch Refinement
    es_query = {
        "query": {
            "bool": {
                "must": [
                    {
                        "ids": {
                            "values": faiss_node_ids  # Use FAISS node IDs
                        }
                    },
                    {
                        "bool": {
                            "should": [
                                {
                                    "match": {
                                        "text": query_text
                                    }
                                },
                                {
                                    "script_score": {
                                        "query": {
                                            "exists": {
                                                "field": "text_embedding"
                                            }
                                        },
                                        "script": {
                                            "source": "cosineSimilarity(params.query_vector, 'text_embedding') + 1.0",
                                            "params": {
                                                "query_vector": query_embedding  # Use the computed query embedding
                                            }
                                        },
                                        "boost": 2.0  # Adjust boost for vector score importance
                                    }
                                }
                            ]
                        }
                    }
                ]
            }
        }
    }
    es_results = es_client.search(index="freelancers", body=es_query)
    return [hit["_id"] for hit in es_results["hits"]["hits"]]
    

   

es_config = {
    "hosts": ["https://localhost:9200"],
    "basic_auth": ("elastic", "fT3WSy=x=G-5dpSkBEB_"),
    "verify_certs": False
}

model_data = {
    "embedding_model": embedding_model,
    "faiss_index": faiss_index_llama,
    "es_config": es_config,
    "hybrid_search": hybrid_faiss_es_search
}

joblib.dump(model_data,"smart_search_model.pkl")
print("All components are loaded in the pkl file lessgoooo")


LLM is explicitly disabled. Using MockLLM.


All components are loaded in the pkl file lessgoooo


In [11]:
import joblib
model = joblib.load("smart_search_model.pkl")
print(model.keys())
print("embedding model:",model.get("embedding_model"))

dict_keys(['embedding_model', 'faiss_index', 'es_config', 'hybrid_search'])
embedding model: model_name='sentence-transformers/all-MiniLM-L6-v2' embed_batch_size=10 callback_manager=<llama_index.core.callbacks.base.CallbackManager object at 0x000001F8844408F0> num_workers=None max_length=256 normalize=True query_instruction=None text_instruction=None cache_folder=None


In [12]:
ground_truth = {
    "python developer": ["F0074", "F0085", "F0115"],
    "machine learning": ["F0048", "F0074","F0080"],
    "react": ["F0064", "F0105","F0112"]
}


In [ ]:
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
from elasticsearch import Elasticsearch
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.core import StorageContext, load_index_from_storage

# Ensure you're using PyTorch by specifying it
embedding_model = HuggingFaceEmbedding(model_name="sentence-transformers/all-MiniLM-L6-v2", device="cpu")

# Load FAISS index and embedding model
storage_context = StorageContext.from_defaults(persist_dir="faiss_index_llama")
faiss_index_llama = load_index_from_storage(storage_context, embed_model=embedding_model, llm=None)

# Create Elasticsearch client
es_client = Elasticsearch()

# Hybrid FAISS + Elasticsearch Search function
def hybrid_faiss_es_search(query_text, faiss_index_llama, es_client, embedding_model, index_name="freelancers", top_k=10):
    """
    Performs a hybrid search using LlamaIndex FAISS index and Elasticsearch.
    """
    # 1. FAISS Retrieval (using LlamaIndex)
    query_embedding = embedding_model.get_query_embedding(query_text)
    
    # Create query engine with llm=None to disable LLM usage
    query_engine = faiss_index_llama.as_query_engine(
        similarity_top_k=top_k,
        llm=None  # Explicitly disable LLM
    )
    response = query_engine.query(query_text)  # Pass the text, not embedding
    nodes_with_scores = response.source_nodes
    faiss_node_ids = [node.node.id_ for node in nodes_with_scores]  # Use id_ instead of node_id
    print("FAISS node IDs:", faiss_node_ids)

    # 2. Elasticsearch Refinement
    es_query = {
        "query": {
            "bool": {
                "must": [
                    {
                        "ids": {
                            "values": faiss_node_ids  # Use FAISS node IDs
                        }
                    },
                    {
                        "bool": {
                            "should": [
                                {
                                    "match": {
                                        "text": query_text
                                    }
                                },
                                {
                                    "script_score": {
                                        "query": {
                                            "exists": {
                                                "field": "text_embedding"
                                            }
                                        },
                                        "script": {
                                            "source": "cosineSimilarity(params.query_vector, 'text_embedding') + 1.0",
                                            "params": {
                                                "query_vector": query_embedding  # Use the computed query embedding
                                            }
                                        },
                                        "boost": 2.0  # Adjust boost for vector score importance
                                    }
                                }
                            ]
                        }
                    }
                ]
            }
        }
    }

    print("Elasticsearch Query:", es_query)  # Debug print
    es_results = es_client.search(index=index_name, body=es_query)
    predicted_ids = [hit['_id'] for hit in es_results['hits']['hits']]
    print("Predicted Document IDs:", predicted_ids)

    # 3. Result Combination and Re-ranking
    # Use the Elasticsearch score as the final score
    return predicted_ids

# Mock ground truth dictionary for testing
ground_truth = {
    "query1": ["doc1", "doc2"],  # Expected doc IDs for query1
    "query2": ["doc3", "doc4"],  # Expected doc IDs for query2
}

# Store predictions and true values
y_true = []  # Actual (ground truth) labels
y_pred = []  # Model-predicted labels

# Iterate over the queries and compare the results
for query, expected_ids in ground_truth.items():
    # Call the hybrid_faiss_es_search function
    retrieved_results = hybrid_faiss_es_search(query, faiss_index_llama, es_client, embedding_model)

    # Convert to binary labels (1 if correct, 0 if incorrect)
    for doc_id in expected_ids:
        y_true.append(1)  # Expected to be retrieved
        # If doc_id is in the retrieved results, it's a correct prediction (1)
        y_pred.append(1 if doc_id in retrieved_results else 0)

# Compute Accuracy
accuracy = accuracy_score(y_true, y_pred)
print(f"Model Accuracy: {accuracy:.2f}")

# Confusion Matrix
cm = confusion_matrix(y_true, y_pred)
print("Confusion Matrix:\n", cm)

# Classification Report
print(classification_report(y_true, y_pred))


RuntimeError: Failed to import transformers.integrations.integration_utils because of the following error (look up to see its traceback):
Failed to import transformers.modeling_utils because of the following error (look up to see its traceback):
No module named 'tensorflow'